In [133]:
import os

import matplotlib.pyplot as plt
import pyLDAvis

from gensim.corpora import Dictionary

import spacy
from math import nan
from itertools import chain
import gensim.models
from gensim.parsing.preprocessing import *
import pandas as pd

import nltk


# !python -m spacy download en_core_web_md -qq
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns

sns.set()
import spacy
import pyLDAvis.gensim_models

pyLDAvis.enable_notebook()  # Visualise inside a notebook
from gensim.corpora.dictionary import Dictionary
from gensim.models import LdaMulticore
from gensim.models import CoherenceModel

# nltk.download('omw-1.4')
# nltk.download('wordnet')
# nlp = spacy.load('en_core_web_sm')
stop_words = gensim.parsing.preprocessing.STOPWORDS
pd.set_option('display.max_rows', 500)
pd.set_option('display.max_columns', 50)
pd.set_option('display.width', 1000)

^C


In [134]:
import sqlite3 as sql

conn = sql.connect('data/outputDatabase.sqlite')


In [138]:
df = pd.read_sql('SELECT * FROM train', conn)

df['author_text'] = df['author'] + ' ' + df['title'] + ' ' + df['text']

df.drop(columns=['author', 'title', 'text', 'index'], inplace=True)

df.head()
# df['out'] = df['text'].apply(preprocess_text)
# df['out'][0]

label                                        author_text
0      1  Darrell Lucus House Dem Aide: We Didn’t Even S...
1      0  Daniel J. Flynn FLYNN: Hillary Clinton, Big Wo...
2      1  Consortiumnews.com Why the Truth Might Get You...
3      1  Jessica Purkiss 15 Civilians Killed In Single ...
4      1  Howard Portnoy Iranian woman jailed for fictio...

In [139]:
stop_words = gensim.parsing.preprocessing.STOPWORDS

from string import punctuation


def preprocess_text(text):
    text = text.lower()  # Lowercase text
    # text = re.sub(f"[{re.escape(punctuation)}]", "", remove_stopwords(text))

    text = remove_stopwords(text, stopwords=[stop_words, removal])
    text = strip_non_alphanum(text)
    text = strip_short(text, 3)
    text = "".join(text)  # Remove extra spaces, tabs, and new lines
    return text


# a=df['text'].apply(lambda x : [''.join(w) for w in x.split() if w not in stop_words])
df['author_text_clean'] = df['author_text'].apply(preprocess_text)
df

label                                        author_text                                  author_text_clean
0          1  Darrell Lucus House Dem Aide: We Didn’t Even S...  darrell lucus house dem aide didn even see com...
1          0  Daniel J. Flynn FLYNN: Hillary Clinton, Big Wo...  daniel flynn flynn hillary clinton big woman c...
2          1  Consortiumnews.com Why the Truth Might Get You...  consortiumnews com why the truth might get you...
3          1  Jessica Purkiss 15 Civilians Killed In Single ...  jessica purkiss civilians killed single airstr...
4          1  Howard Portnoy Iranian woman jailed for fictio...  howard portnoy iranian woman jailed for fictio...
...      ...                                                ...                                                ...
20782      0  Jerome Hudson Rapper T.I.: Trump a ’Poster Chi...  jerome hudson rapper trump poster child for wh...
20783      0  Benjamin Hoffman N.F.L. Playoffs: Schedule, Ma...  benjamin hoffman playoffs schedule matchups an...
20784      0  Michael J. de la Merced and Rachel Abrams Macy...  michael merced and rachel abrams macy said rec...
20785      1  Alex Ansary NATO, Russia To Hold Parallel Exer...  alex ansary nato russia hold parallel exercise...
20786      1  David Swanson What Keeps the F-35 Alive David ...  david swanson what keeps the alive david swans...

[20787 rows x 3 columns]

In [140]:
def is_ascii(letter):
    letter = letter[0]

    if letter in string.ascii_letters:
        return True
    return False


df['rem'] = df['author_text_clean'].apply(is_ascii)

df = df[df['rem'] == True]


In [141]:

# CUSTOM_FILTERS = [
#     remove_stopwords,
#     strip_non_alphanum,
#     strip_multiple_whitespaces,
#     strip_short,
#     stem_text
# ]

tokens = [preprocess_string(doc) for doc in df['author_text_clean']]
tokens

[['darrel',
  'lucu',
  'hous',
  'dem',
  'aid',
  'comei',
  'letter',
  'jason',
  'chaffetz',
  'tweet',
  'hous',
  'dem',
  'aid',
  'comei',
  'letter',
  'jason',
  'chaffetz',
  'tweet',
  'darrel',
  'lucu',
  'octob',
  'subscrib',
  'jason',
  'chaffetz',
  'stump',
  'american',
  'fork',
  'utah',
  'imag',
  'courtesi',
  'michael',
  'jollei',
  'avail',
  'creativ',
  'common',
  'licens',
  'apolog',
  'keith',
  'olbermann',
  'doubt',
  'worst',
  'person',
  'world',
  'week',
  'fbi',
  'director',
  'jame',
  'comei',
  'accord',
  'hous',
  'democrat',
  'aid',
  'look',
  'like',
  'know',
  'second',
  'worst',
  'person',
  'turn',
  'comei',
  'sent',
  'infam',
  'letter',
  'announc',
  'fbi',
  'look',
  'email',
  'relat',
  'hillari',
  'clinton',
  'email',
  'server',
  'rank',
  'democrat',
  'relev',
  'committe',
  'hear',
  'comei',
  'tweet',
  'republican',
  'committe',
  'chairmen',
  'know',
  'comei',
  'notifi',
  'republican',
  'chairmen'

In [142]:
df['tokens'] = tokens

all_words = list(chain.from_iterable(df['tokens']))
num_words = len(set(all_words))

print(
    f'all words: {len(all_words)}\n'
    f'unique words: {num_words}'
)

removal = []

for word in set(all_words):
    # word = strip_non_alphanum(word)
    word = word.lstrip()
    # print(word)
    if not is_ascii(word[0]):
        removal.append(word)

removal
# for i in all_words:
#     for w in removal:
#         if w in i:
#             all_words.remove(w)


C:\Users\danie\AppData\Local\Temp/ipykernel_4900/4118519123.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df['tokens'] = tokens


all words: 7624820
unique words: 130747


['стиль',
 'единиц',
 'коалицию',
 'федеральном',
 'закупок',
 'объявления',
 'выполните',
 'водомета',
 'перевели',
 'августовского',
 'وأضاف',
 'дал',
 'авось',
 'الصعيد',
 'мозгах',
 'супермаркеты',
 'ближайшая',
 'политическом',
 'пхеньяна',
 'انتشار',
 'планы',
 'отдаленную',
 'тихоокеанского',
 'подземка',
 'русской',
 'الإيطالية',
 'موشات',
 'подписчиков',
 'взятое',
 'расширены',
 'формате',
 'œthe',
 'أكد',
 'единогласно',
 'гигиены',
 'религиозных',
 'морях',
 'антарктике',
 'диалогу',
 'известиям',
 'пространство',
 'صنعاء',
 'одинаковую',
 'окружение',
 'íntima',
 'мигом',
 'لرويترز',
 'حرة',
 'уместно',
 'проводниками',
 'главными',
 'платить',
 'блокировки',
 'пастух',
 'ненужное',
 'материала',
 'φόβοι',
 'обсуждению',
 'брюсселя',
 'таиландско',
 'прибыльное',
 'أصيبا',
 'флешки',
 'секешфехерваре',
 'радикальным',
 'укрывающегося',
 'попытался',
 'грабли',
 'конкуренцию',
 'экипаж',
 'черным',
 'الملقب',
 'предстоит',
 'понимают',
 'допускающее',
 'контратаковать',
 'м

In [147]:
removal = set(removal)
all_words = (w for w in removal if w not in removal)

In [153]:
# df.drop(columns=['rem'], inplace=True)
df

label                                        author_text                                  author_text_clean                                             tokens
0          1  Darrell Lucus House Dem Aide: We Didn’t Even S...  darrell lucus house dem aide didn even see com...  [darrel, lucu, hous, dem, aid, comei, letter, ...
1          0  Daniel J. Flynn FLYNN: Hillary Clinton, Big Wo...  daniel flynn flynn hillary clinton big woman c...  [daniel, flynn, flynn, hillari, clinton, big, ...
2          1  Consortiumnews.com Why the Truth Might Get You...  consortiumnews com why the truth might get you...  [consortiumnew, com, truth, fire, truth, fire,...
3          1  Jessica Purkiss 15 Civilians Killed In Single ...  jessica purkiss civilians killed single airstr...  [jessica, purkiss, civilian, kill, singl, airs...
4          1  Howard Portnoy Iranian woman jailed for fictio...  howard portnoy iranian woman jailed for fictio...  [howard, portnoi, iranian, woman, jail, fictio...
...      ...                                                ...                                                ...                                                ...
20782      0  Jerome Hudson Rapper T.I.: Trump a ’Poster Chi...  jerome hudson rapper trump poster child for wh...  [jerom, hudson, rapper, trump, poster, child, ...
20783      0  Benjamin Hoffman N.F.L. Playoffs: Schedule, Ma...  benjamin hoffman playoffs schedule matchups an...  [benjamin, hoffman, playoff, schedul, matchup,...
20784      0  Michael J. de la Merced and Rachel Abrams Macy...  michael merced and rachel abrams macy said rec...  [michael, merc, rachel, abram, maci, said, rec...
20785      1  Alex Ansary NATO, Russia To Hold Parallel Exer...  alex ansary nato russia hold parallel exercise...  [alex, ansari, nato, russia, hold, parallel, e...
20786      1  David Swanson What Keeps the F-35 Alive David ...  david swanson what keeps the alive david swans...  [david, swanson, keep, aliv, david, swanson, a...

[20728 rows x 4 columns]

In [155]:
# df.reset_index().to_feather('data/df_concat.feather')
df.to_csv('data/train_processed.csv', index=False)
# df.to_csv('data/train_processed.csv', index=False)
# df.reset_index(drop=True, inplace=True)
# df = df.iloc[:, 1:]

In [38]:
# df.to_feather('data/df_concat.feather')
# df.to_csv('data/train_processed.csv', index=False)

df = pd.read_sql('SELECT * FROM train_processed', conn)

In [189]:
df_fake = df[df['label'] == 0]
fake_words = list(chain.from_iterable(df_fake['tokens']))


# print(fake_words)

df_real = df[df['label'] == 1]
real_words = list(chain.from_iterable(df_real['tokens']))
from nltk.stem import PorterStemmer, WordNetLemmatizer
from nltk.tokenize import word_tokenize


# tf_idf = models.TfidfModel(mycorpus)
#
# trans_tf_idf = tf_idf[mycorpus]
# print(trans_tf_idf)

In [199]:
d_fake = Dictionary(df_fake['tokens'])
d_real = Dictionary(df_real['tokens'])
mydict = Dictionary(df['tokens'])
# fake_tokens = df_fake['tokens'].to_list()


fake_bow = [d_fake.doc2bow(doc) for doc in df_fake['tokens']]
real_bow = [d_real.doc2bow(doc) for doc in df_real['tokens']]
# d_real = Dictionary(real_words)
# real_bow = [d_real.doc2bow(doc) for doc in real_words]

In [192]:
# mydict_fake, mydict_real = \
#     Dictionary(fake_corpus).filter_extremes(no_below=5), Dictionary(real_corpus).filter_extremes(no_below=5)
# bow_fake = [dict_fake.doc2bow(doc) for doc in corpus_fake]
# bow_real = [dict_real.doc2bow(doc) for doc in corpus_real]

mycorpus = [mydict.doc2bow(doc, allow_update=True) for doc in tokens]

# word_counts = [[(mydict[id], count) for id, count in line]
#                for line in mycorpus]

[['darrel',
  'lucu',
  'hous',
  'dem',
  'aid',
  'comei',
  'letter',
  'jason',
  'chaffetz',
  'tweet',
  'hous',
  'dem',
  'aid',
  'comei',
  'letter',
  'jason',
  'chaffetz',
  'tweet',
  'darrel',
  'lucu',
  'octob',
  'subscrib',
  'jason',
  'chaffetz',
  'stump',
  'american',
  'fork',
  'utah',
  'imag',
  'courtesi',
  'michael',
  'jollei',
  'avail',
  'creativ',
  'common',
  'licens',
  'apolog',
  'keith',
  'olbermann',
  'doubt',
  'worst',
  'person',
  'world',
  'week',
  'fbi',
  'director',
  'jame',
  'comei',
  'accord',
  'hous',
  'democrat',
  'aid',
  'look',
  'like',
  'know',
  'second',
  'worst',
  'person',
  'turn',
  'comei',
  'sent',
  'infam',
  'letter',
  'announc',
  'fbi',
  'look',
  'email',
  'relat',
  'hillari',
  'clinton',
  'email',
  'server',
  'rank',
  'democrat',
  'relev',
  'committe',
  'hear',
  'comei',
  'tweet',
  'republican',
  'committe',
  'chairmen',
  'know',
  'comei',
  'notifi',
  'republican',
  'chairmen'

In [170]:
# flat_counts = [i for s in word_counts for i in s]
# flat_counts

[('ablaz', 1),
 ('abus', 1),
 ('accord', 3),
 ('act', 1),
 ('actual', 1),
 ('advanc', 1),
 ('agenc', 1),
 ('aid', 6),
 ('american', 1),
 ('anchor', 1),
 ('announc', 1),
 ('answer', 1),
 ('anthoni', 1),
 ('apolog', 1),
 ('appar', 2),
 ('appear', 1),
 ('attempt', 1),
 ('avail', 1),
 ('basic', 1),
 ('bipartisanship', 1),
 ('boss', 1),
 ('briefli', 1),
 ('bui', 1),
 ('burton', 1),
 ('carolina', 1),
 ('case', 4),
 ('chaffetz', 15),
 ('chairman', 2),
 ('chairmen', 4),
 ('charismat', 1),
 ('check', 1),
 ('christian', 2),
 ('classifi', 1),
 ('click', 1),
 ('clinton', 1),
 ('colleagu', 1),
 ('colleg', 1),
 ('comei', 11),
 ('committe', 7),
 ('common', 1),
 ('connect', 2),
 ('consid', 1),
 ('contain', 1),
 ('control', 1),
 ('cook', 1),
 ('cooler', 1),
 ('counterpart', 1),
 ('cours', 1),
 ('courtesi', 2),
 ('creativ', 1),
 ('cum', 1),
 ('daili', 2),
 ('dan', 1),
 ('darrel', 6),
 ('darrelllucu', 1),
 ('deaf', 1),
 ('decenc', 1),
 ('dem', 3),
 ('democrat', 8),
 ('desir', 1),
 ('develop', 1),
 ('dir'

In [171]:
# import pickle
#
# pickle.dump(mycorpus, open('mycorpus.pkl', 'wb'))
# mydict.save('corp_dict.gensim')

In [200]:
# from gensim import models, similarities
import numpy as np
import pyLDAvis
import pyLDAvis.gensim_models as gensimvis

pyLDAvis.enable_notebook()

# tf_idf = models.TfidfModel(mycorpus)
lda_model = LdaMulticore(
    corpus=fake_bow,
    id2word=d_fake,
    random_state=100,
    num_topics=7,
    passes=10,
    chunksize=1000,
    batch=False,
    alpha='asymmetric',
    decay=0.5,
    offset=64,
    eta=None,
    eval_every=0,
    iterations=100,
    gamma_threshold=0.001,
    per_word_topics=True
)

# save the model
# lda_model.save('lda_model.model')
# for item in tf_idf[mycorpus]:
#         print([[mydict[id], np.around(freq, decimals=2)] for id, freq in item])
vis = gensimvis.prepare(lda_model, fake_bow, d_fake)
vis

C:\Users\danie\anaconda3\envs\proj\lib\site-packages\pyLDAvis\_prepare.py:247: FutureWarning: In a future version of pandas all arguments of DataFrame.drop except for the argument 'labels' will be keyword-only.
  by='saliency', ascending=False).head(R).drop('saliency', 1)


PreparedData(topic_coordinates=              x         y  topics  cluster       Freq
topic                                                
4      0.115732  0.022922       1        1  52.265706
1      0.046419 -0.060239       2        1  18.201823
0      0.062569 -0.042402       3        1  15.378703
5      0.071504  0.060979       4        1  13.969635
2     -0.078770  0.010033       5        1   0.095605
6     -0.079071  0.007273       6        1   0.049635
3     -0.138382  0.001434       7        1   0.038893, topic_info=       Term          Freq         Total Category  logprob  loglift
190    said  63983.000000  63983.000000  Default  30.0000  30.0000
223   trump  34214.000000  34214.000000  Default  29.0000  29.0000
155     new  34079.000000  34079.000000  Default  28.0000  28.0000
217    time  23481.000000  23481.000000  Default  27.0000  27.0000
247    year  20521.000000  20521.000000  Default  26.0000  26.0000
..      ...           ...           ...      ...      ...      ...
275    live      0.890143   6426.625796   Topic7  -7.5604  -1.0325
44     come      0.906229   7185.199729   Topic7  -7.5425  -1.1261
235    want      0.927904   8829.218393   Topic7  -7.5189  -1.3085
392  includ      0.898896   9058.972986   Topic7  -7.5507  -1.3660
944   offic      0.890752   8298.474821   Topic7  -7.5598  -1.2874

[603 rows x 6 columns], token_table=       Topic      Freq            Term
term                                  
10696      1  0.956180          abedin
10696      2  0.019514          abedin
10696      3  0.013009          abedin
10696      4  0.006505          abedin
22137      1  0.027011  abfalecbaldwin
...      ...       ...             ...
54021      4  0.352507             غير
62665      1  0.317040             قوة
62665      2  0.317040             قوة
62665      3  0.317040             قوة
62665      4  0.317040             قوة

[2079 rows x 3 columns], R=30, lambda_step=0.01, plot_opts={'xlab': 'PC1', 'ylab': 'PC2'}, topic_order=[5, 2, 1, 6, 3, 7, 4])

In [201]:
html = pyLDAvis.prepared_data_to_html(vis)

with open('figures/data_vis_fake.html', 'w+') as file:
    file.write(html)

In [208]:
import tensorflow as tf
import pandas as pd
import numpy as np
import matplotlib.pyplot as plt
import seaborn as sns
from sklearn.model_selection import train_test_split as tts

import nltk
import re
from nltk.stem import PorterStemmer, WordNetLemmatizer
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize, sent_tokenize
import gensim
from gensim.utils import simple_preprocess
from gensim.parsing.preprocessing import STOPWORDS as stop_words
import keras
from keras.preprocessing.text import one_hot, Tokenizer

from keras.preprocessing.sequence import pad_sequences
from keras.models import Sequential
from keras.layers import Dense, Flatten, Embedding, Input, LSTM, Conv1D, MaxPool1D, Bidirectional
from keras.models import Model

x_train, x_test, y_train, y_test = tts(df['author_text_clean'], df['label'], test_size=0.2)

tokenizer = Tokenizer(num_words=num_words)
tokenizer.fit_on_texts(x_train)
trainings = tokenizer.texts_to_sequences(x_train)
testings = tokenizer.texts_to_sequences(x_test)

padded_train = pad_sequences(trainings, maxlen=40, padding='post', truncating='post')
padded_test = pad_sequences(testings, maxlen=40, truncating='post')


In [ ]:
model = Sequential()
model.add(Embedding(num_words, output_dim=128))
model.add(Bidirectional(LSTM(128)))

model.add(Dense(128, activation='relu'))
model.add(Dense(1, activation='sigmoid'))
model.compile(optimizer='adam', loss='binary_crossentropy', metrics=['accuracy'])
model.summary()

In [ ]:
y_train = np.asarray(y_train)

model.fit(
    padded_train,
    y_train,
    batch_size=64,
    validation_split=0.1,
    epochs=2,
    validation_data=(x_test, y_test),
    use_multiprocessing=True
)


In [ ]:
model.save('fakenews_model.model')

In [ ]:
make_pred = model.predict(padded_test)

preds = []

preds = [1 if make_pred[i].item() > 0.5 else 0 for i in range(len(make_pred))]

print(preds)

In [ ]:
from sklearn.metrics import accuracy_score

accuracy = accuracy_score(list(y_test), preds)

print("Model Accuracy : ", accuracy)

In [78]:
lda_model = LdaMulticore(
    corpus=fake_bow,
    id2word=d_fake,
    random_state=100,
    num_topics=7,
    passes=10,
    chunksize=1000,
    batch=False,
    alpha='asymmetric',
    decay=0.5,
    offset=64,
    eta=None,
    eval_every=0,
    iterations=100,
    gamma_threshold=0.001,
    per_word_topics=True
)
from sklearn.feature_extraction.text import CountVectorizer

small_vectorizer = CountVectorizer(stop_words=stop_words, max_features=50_000)

lda_topic_matrix = lda_model.fit_transform(small_document_term_matrix)

'Darrell Lucus House Dem Aide: We Didn’t Even See Comey’s Letter Until Jason Chaffetz Tweeted It House Dem Aide: We Didn’t Even See Comey’s Letter Until Jason Chaffetz Tweeted It By Darrell Lucus October 30, 2016 Subscribe Jason Chaffetz stump American Fork, Utah ( image courtesy Michael Jolley, available Creative Commons-BY license) With apologies Keith Olbermann, doubt Worst Person The World week–FBI Director James Comey. But according House Democratic aide, looks like know second-worst person well. It turns Comey sent now-infamous letter announcing FBI looking emails related Hillary Clinton’s email server, ranking Democrats relevant committees didn’t hear Comey. They tweet Republican committee chairmen. As know, Comey notified Republican chairmen Democratic ranking members House Intelligence, Judiciary, Oversight committees agency reviewing emails recently discovered order contained classified information. Not long letter went out, Oversight Committee Chairman Jason Chaffetz set pol